In [2]:
import os, itertools, pickle
import numpy as np
import pandas as pd

from pyecharts.globals import ThemeType, CurrentConfig, GeoType, NotebookType
from pyecharts import options as opts
from pyecharts.charts import Geo
from pyecharts.globals import ChartType
from pyecharts.datasets import register_url

from pyecharts.render import make_snapshot
from snapshot_selenium import snapshot

from sklearn import impute, preprocessing

register_url("https://echarts-maps.github.io/echarts-china-misc-js/")

CurrentConfig.NOTEBOOK_TYPE = NotebookType.JUPYTER_NOTEBOOK

# pip install svglib
RAWDATA_PATH = "../rawData/"

In [3]:
# Get mean of air pollution
ap_d = {
    "PM25":['PM25_year_2015','PM25_year_2016','PM25_year_2017','PM25_year_2018'],
    "O3":['O3_year_2015','O3_year_2016','O3_year_2017','O3_year_2018'],
    "NO2":['NO2_year_2015','NO2_year_2016','NO2_year_2017','NO2_year_2018'],
    "NDVI_250":['NDVI_2015_250','NDV_2016_250','NDVI_2017_250','NDVI_2018_250'],
    "NDVI_500":['NDVI_2015_500','NDVI_2016_500','NDVI_2017_500','NDVI_2018_500'],
    "NDVI_1000":['NDVI_2015_1000','NDVI_2016_1000','NDVI_2017_1000','NDVI_2018_1000'],
    "PM1_wj":['wj_PM1_2014','wj_PM1_2015','wj_PM1_2016','wj_PM1_2017','wj_PM1_2018'],
    "PM10_wj":['wj_PM10_2014','wj_PM10_2015','wj_PM10_2016','wj_PM10_2017','wj_PM10_2018'],
    "NO2_wj":['wj_NO2_2014','wj_NO2_2015','wj_NO2_2016','wj_NO2_2017','wj_NO2_2018'],
    "t2m":['t2m_mean2013','t2m_mean2014','t2m_mean2015','t2m_mean2016','t2m_mean2017','t2m_mean2018']
}

province_english_map = {'重庆市':"Chongqing", '四川省':"Sichuan", 
                        '贵州省':"Guizhou", '云南省':"Yunnan", 
                        '西藏自治区':"Xizang"}

with open(os.path.join(RAWDATA_PATH, "analysis_data_no_scale.pickle"), "rb") as f:
    raw_data = pickle.load(f)

In [4]:
ap_d.keys()

dict_keys(['PM25', 'O3', 'NO2', 'NDVI_250', 'NDVI_500', 'NDVI_1000', 'PM1_wj', 'PM10_wj', 'NO2_wj', 't2m'])

In [8]:
ap_name = 'PM25'
data_sel = raw_data[['lat', 'lon', ap_name]].copy()

data_sel = data_sel.drop_duplicates().copy()

data_sel["LocName"] = data_sel.index.astype(str)

geo = Geo(init_opts=opts.InitOpts(
    width='800px', # 图表画布宽度，css 长度单位
    height='600px', # 图表画布高度，css 长度单位
    renderer="svg", # canvas Or svg
    #renderer="canvas", # canvas Or svg
    theme="white", # https://blog.csdn.net/qq_41595507/article/details/102947622
),
          # 是否忽略不存在的坐标，默认值为 False，即不忽略
          is_ignore_nonexistent_coord = False)

geo.add_schema(maptype='西南', 
               )

for index in data_sel.index:
    geo.add_coordinate(data_sel.loc[index, "LocName"], data_sel.loc[index, "lon"], data_sel.loc[index, "lat"])

    
geo.add(
        ap_name,
        data_sel[["LocName", ap_name]].values,
        #type_=ChartType.HEATMAP,
    type_="scatter",
    symbol_size=8
    )


geo.set_series_opts(label_opts=opts.LabelOpts(is_show=False))
geo.set_global_opts(
    legend_opts=opts.LegendOpts(is_show=True),
    visualmap_opts=opts.VisualMapOpts(max_=data_sel[ap_name].max(), 
                                      min_=data_sel[ap_name].min(),
                                      is_piecewise=False, is_calculable=True, range_text=["High", "Low"], pos_top="middle"),
    toolbox_opts=opts.ToolboxOpts(is_show=True), 
    )

geo.render_notebook()
#geo.render("./{}_ProvinceMap.html".format(ap_name))